In [1]:
pip install bayesian-optimization

  Created wheel for bayesian-optimization: filename=bayesian_optimization-1.2.0-cp36-none-any.whl size=11685 sha256=a74251b23225a74bf48357a1848915d946e7fee471c6e016514ed02da2171453
  Stored in directory: /root/.cache/pip/wheels/5a/56/ae/e0e3c1fc1954dc3ec712e2df547235ed072b448094d8f94aec
Successfully built bayesian-optimization


In [14]:
import datetime as dt
import statistics 

import numpy as np
import pandas as pd
import pandas_datareader as web
import tensorflow as tf
import matplotlib.pyplot as plt

from sklearn.preprocessing import MinMaxScaler
from tensorflow.keras.models import Sequential
from tensorflow.keras.callbacks import EarlyStopping
from tensorflow.keras.layers import Dense, LSTM, Dropout, LeakyReLU,PReLU

from bayes_opt import BayesianOptimization

# switch between daily or hourly data
DATA = "daily"
# DATA = "hourly"

if DATA == "daily":
  silver_name = "SI=F"
elif DATA == "hourly":
  silver_name = "si.f.txt"


In [32]:
start_data = dt.datetime(2008, 1, 1)
end_data = dt.datetime(2020,1,1)

# list of all observed variables
observed_data = ['SI=F', # silver
                 'PL=F', # platinum
                 'GC=F', # gold
                 'HG=F', # copper
                 'CL=F', # crude oil
                 'NG=F', # natural gas
                 'HO=F', # heating oil               
#                 'C=F', # corn
                 'SB=F', # soybean
#                 'FC=F',
                 'HE=F',
#                 'LC=F',               
                 'NQ=F', # Nasdaq, stock exchange
                 'YM=F',  # Dow Jones index
                 '^RUT', # Russel 2000
                 '^GSPC', # E-Mini S&P 500  
                 '^DJI', # Dow Jones Industrial Average    
                 'ZF=F', # us treasury bonds
                 'ZT=F',
                 'ZB=F', 
#                 'TY=F',
                 'ZN=F',
#                 'ED=F',
                 'EUR=X', # eur usd
                 'JPY=X', # jpy usd
                 'RUB=X', # rub usd
                 'AUD=X', # aus usd
                 'ZAR=X', # rand usd
                 'GBPUSD=X', # dbp usd
                 'EURGBP=x', # eur gbp           
                 'WPM',
                 'AG',
                 'PAAS',
                 'EXK',
                 'HL',
                 'SVM.TO',
                 'FVI.TO',
                 'PAAS.TO',
                 'FR.TO',
                 ]

df  = pd.DataFrame()

for o_d in observed_data:
  tmp_df =  web.DataReader(o_d, 'yahoo', start=start_data, end=end_data)
  tmp_df.rename(columns = {'Adj Close': o_d}, inplace=True)
  tmp_df.drop(['High', 'Low', 'Open', 'Close', 'Volume'], 1, inplace=True)
  if df.empty:
    df = tmp_df # first column
  else:
    df = df.join(tmp_df, how='outer') # other columns

#df.dropna(inplace=True) # drop all rows which are not complete (in Yahoo dataset there are only few data on Sundays)

df.to_csv(r'backup_yahoo.csv', header=True) # create a csv table

In [15]:
def load_data():
  # # Load DataFrame from prepared csv file
  if (DATA == "daily"):
    path_to_df = r'export_yahoo.csv'
    df = pd.read_csv(filepath_or_buffer = path_to_df)
    df['Date'] = pd.to_datetime(df['Date'])
    date_time = df['Date']
    df = df.set_index("Date")
    
  elif (DATA == "hourly"):
    path_to_df = r'export_df.csv'
    df = pd.read_csv(filepath_or_buffer = path_to_df)
    df.dropna(inplace=True) # there should be none row with any Nan value, but better be sure
    df['date'] = pd.to_datetime(df.pop('date'), format='%Y-%m-%d %H:%M:%S')
    date_time = df['date']
    df = df.set_index("date")

  # divide the data
  train_df = df[0:int(len(df)*0.7)] # first 70% data is for training purpose
  val_df = df[int(len(df)*0.7):int(len(df)*0.9)] # %20 is for validation
  test_df = df[int(len(df)*0.9):] # %10 for testing

  col_names = train_df.columns

  # Normalize the data
  scaler = MinMaxScaler()
  train_df = pd.DataFrame(scaler.fit_transform(train_df), columns=col_names)
  val_df = pd.DataFrame(scaler.transform(val_df), columns=col_names)
  test_df = pd.DataFrame(scaler.transform(test_df), columns=col_names)

  return train_df, val_df, test_df

In [16]:
# Different model type creation
def gen_dense_model(f_record, n_col, dropout, units):
  return tf.keras.Sequential([      
      tf.keras.layers.Dense(2*units, activation='relu'),
      tf.keras.layers.Dropout(dropout),
      tf.keras.layers.Dense(f_record*n_col, kernel_initializer=tf.initializers.zeros),
      tf.keras.layers.Lambda(lambda x: x[:, -1:, :]),
      tf.keras.layers.Reshape([f_record, n_col])
    ])

def gen_gru_model(f_record, n_col, dropout, units):
  return tf.keras.Sequential([      
      tf.keras.layers.GRU(units, return_sequences=False, activation='relu', dropout=dropout),
      # tf.keras.layers.Dropout(dropout),
      tf.keras.layers.Dense(f_record*n_col, kernel_initializer=tf.initializers.zeros),
      # tf.keras.layers.Lambda(lambda x: x[:, -1:, :]),
      tf.keras.layers.Reshape([f_record, n_col])
    ])

def gen_lstm_model(f_record, n_col, dropout, units):
  return tf.keras.Sequential([
    tf.keras.layers.LSTM(units, return_sequences=False, dropout=dropout),
    # tf.keras.layers.Dropout(dropout),
    tf.keras.layers.Dense(f_record*n_col, kernel_initializer=tf.initializers.zeros),
    tf.keras.layers.Reshape([f_record, n_col])
  ])

In [17]:
# class for recurrent RNN
class Arr_Rnn(tf.keras.Model):
  def __init__(self, f_records):
    super().__init__()
    self.f_records = f_records

  # insert different types of RNN
  def put_lstm(self, units, dropout):
    self.neuron_cell = tf.keras.layers.LSTMCell(units, recurrent_dropout=dropout)
    self.rnn = tf.keras.layers.RNN(self.neuron_cell, return_state=True)
    self.dense = tf.keras.layers.Dense(num_features)

  def put_gru(self,units, dropout):
    self.neuron_cell = tf.keras.layers.GRUCell(units,recurrent_dropout=dropout)
    self.rnn = tf.keras.layers.RNN(self.neuron_cell, return_state=True)
    self.dense = tf.keras.layers.Dense(num_features)

  def put_simple_rnn(self,units, dropout):
    self.neuron_cell = tf.keras.layers.SimpleRNNCell(units, recurrent_dropout=dropout)
    self.rnn = tf.keras.layers.RNN(self.neuron_cell, return_state=True)
    self.dense = tf.keras.layers.Dense(num_features)

  def put_stacked_rnn(self, units, dropout):
    rnn_cells = [tf.keras.layers.LSTMCell(units, recurrent_dropout=dropout) for _ in range(2)]
    self.neuron_cell = tf.keras.layers.StackedRNNCells(rnn_cells)
    self.rnn = tf.keras.layers.RNN(self.neuron_cell, return_state=True)
    self.dense = tf.keras.layers.Dense(num_features)

  # warmup before the predictions itself
  def warmup(self, inputs):
    x, *state = self.rnn(inputs)
    prediction = self.dense(x)
    return prediction, state

  # prediction itself
  def call(self, inputs, training=None):
    predictions = []
    prediction, state = self.warmup(inputs)
    predictions.append(prediction)

    for n in range(1, self.f_records):
      # x = prediction
      x, state = self.neuron_cell(prediction, states=state,
                                training=training)
      prediction = self.dense(x)
      predictions.append(prediction)

    predictions = tf.stack(predictions)
    predictions = tf.transpose(predictions, [1, 0, 2])
    return predictions

In [18]:
# creates windows which can be used to train and test the models
# done according to tutorial from TensorFlow website
lass WindowGenerator():
  def __init__(self, input_width, label_width, shift,
               train_df, val_df, test_df,
               predicted_col=None):
    # Store the raw data.
    self.train_df = train_df
    self.val_df = val_df
    self.test_df = test_df

    # Work out the label column indices.
    self.predicted_col = predicted_col
    if predicted_col is not None:
      self.label_columns_indices = {name: i for i, name in enumerate(predicted_col)}
    self.index_col = {name: i for i, name in enumerate(train_df.columns)}

    # Work out the window parameters.
    self.input_width = input_width
    self.label_width = label_width
    self.shift = shift
    self.total_window_size = input_width + shift
    self.input_slice = slice(0, input_width)
    self.input_indices = np.arange(self.total_window_size)[self.input_slice]

    self.label_start = self.total_window_size - self.label_width
    self.labels_slice = slice(self.label_start, None)
    self.label_indices = np.arange(self.total_window_size)[self.labels_slice]
        
  def split_window(self, features):
    inputs = features[:, self.input_slice, :]
    labels = features[:, self.labels_slice, :]
    if self.predicted_col is not None:
      labels = tf.stack( [labels[:, :, self.index_col[name]] 
                          for name in self.predicted_col], axis=-1)

    inputs.set_shape([None, self.input_width, None])
    labels.set_shape([None, self.label_width, None])

    return inputs, labels

  def make_dataset(self, data):
    data = np.array(data, dtype=np.float32)
    ds = tf.keras.preprocessing.timeseries_dataset_from_array(
        data=data,
        targets=None,
        sequence_length=self.total_window_size,
        sequence_stride=1,
        shuffle=True,
        batch_size=32,)

    ds = ds.map(self.split_window)

    return ds

  @property
  def example(self):
    """Get and cache an example batch of `inputs, labels` for plotting."""
    result = getattr(self, '_example', None)
    if result is None:
      # No example batch was found, so get one from the `.train` dataset
      result = next(iter(self.train))
      # And cache it for next time
      self._example = result
    return result


  def plot(self, model=None, plot_col=silver_name, max_subplots=3):
    inputs, labels = self.example
    plt.figure(figsize=(12, 8))
    plot_col_index = self.index_col[plot_col]
    max_n = min(max_subplots, len(inputs))
    for n in range(max_n):
      plt.subplot(3, 1, n+1)
      plt.ylabel(f'{plot_col} [normed]')
      plt.plot(self.input_indices, inputs[n, :, plot_col_index],
              label='Inputs', marker='.', zorder=-10)

      if self.predicted_col:
        label_col_index = self.label_columns_indices.get(plot_col, None)
      else:
        label_col_index = plot_col_index

      if label_col_index is None:
        continue

      plt.scatter(self.label_indices, labels[n, :, label_col_index],
                  edgecolors='k', label='Labels', c='#2ca02c', s=64)
      if model is not None:
        predictions = model(inputs)
        plt.scatter(self.label_indices, predictions[n, :, label_col_index],
                    marker='X', edgecolors='k', label='Predictions',
                    c='#ff7f0e', s=64)

      if n == 0:
        plt.legend()

    plt.xlabel(plot_col)

  @property
  def train(self):
    return self.make_dataset(self.train_df)

  @property
  def val(self):
    return self.make_dataset(self.val_df)

  @property
  def test(self):
    return self.make_dataset(self.test_df)

MAX_EPOCHS = 20

def compile_and_fit(model, window, patience=2, opt=tf.optimizers.Adam()):

  early_stopping = tf.keras.callbacks.EarlyStopping(monitor='val_loss',
                                                    patience=patience,
                                                    mode='min')

  model.compile(loss=tf.losses.MeanSquaredError(),
                optimizer=opt,
                metrics=[tf.metrics.MeanAbsoluteError()])
  compiled_model = model.fit(window.train, epochs=MAX_EPOCHS,
                      validation_data=window.val,
                      callbacks=[early_stopping],
                      verbose = 0)
  return compiled_model

In [ ]:
multi_val_performance = {}
multi_performance = {}

train_df, val_df, test_df = load_data()

num_features = train_df.shape[1]


input_w = 64
if DATA == "daily":
  output_w = 14
else:
  output_w = 24

multi_window = WindowGenerator(input_width=input_w,
                               train_df=train_df, val_df=val_df, test_df=test_df,
                               label_width=output_w,
                               shift=output_w)

dropout = 0.1
units = 64

# run each neuron network type and store the results

# Dense
dense_model = gen_dense_model(output_w, num_features, dropout, units);

history = compile_and_fit(dense_model, multi_window)
multi_val_performance['Dense'] = dense_model.evaluate(multi_window.val)
multi_performance['Dense'] = dense_model.evaluate(multi_window.test, verbose=0)

# GRU
gru_model = gen_gru_model(output_w, num_features, dropout, units)

history = compile_and_fit(gru_model, multi_window)
multi_val_performance['GRU'] = gru_model.evaluate(multi_window.val)
multi_performance['GRU'] = gru_model.evaluate(multi_window.test, verbose=0)

# LSTM
lstm_model = gen_lstm_model(output_w, num_features, dropout, units)

history = compile_and_fit(lstm_model, multi_window)
multi_val_performance['LSTM'] = lstm_model.evaluate(multi_window.val)
multi_performance['LSTM'] = lstm_model.evaluate(multi_window.test, verbose=0)

# Autoregressive LSTM
arr_lstm_model = Arr_Rnn(output_w)
arr_lstm_model.put_lstm(64, dropout)
prediction, state = arr_lstm_model.warmup(multi_window.example[0])

history = compile_and_fit(arr_lstm_model, multi_window)
multi_val_performance['AR LSTM'] = arr_lstm_model.evaluate(multi_window.val)
multi_performance['AR LSTM'] = arr_lstm_model.evaluate(multi_window.test, verbose=0)

# Autoregressive GRU
arr_gru_model = Arr_Rnn(output_w)
arr_gru_model.put_gru(units, dropout)
prediction, state = arr_gru_model.warmup(multi_window.example[0])

history = compile_and_fit(arr_gru_model, multi_window)
multi_val_performance['AR GRU'] = arr_gru_model.evaluate(multi_window.val)
multi_performance['AR GRU'] = arr_gru_model.evaluate(multi_window.test, verbose=0)

# Autoregressive simple RNN
arr_simple_rnn_model = Arr_Rnn(output_w)
arr_simple_rnn_model.put_simple_rnn(units, dropout)
prediction, state = arr_simple_rnn_model.warmup(multi_window.example[0])

history = compile_and_fit(arr_simple_rnn_model, multi_window)
multi_val_performance['AR Simple RNN'] = arr_simple_rnn_model.evaluate(multi_window.val)
multi_performance['AR Simple RNN'] = arr_simple_rnn_model.evaluate(multi_window.test, verbose=0) 

# Autoregressive stacked RNN
arr_stacked_rnn_model = Arr_Rnn(output_w)
arr_stacked_rnn_model.put_stacked_rnn(units, dropout)
prediction, state = arr_simple_rnn_model.warmup(multi_window.example[0])

history = compile_and_fit(arr_stacked_rnn_model, multi_window)
multi_val_performance['AR Stack RNN'] = arr_stacked_rnn_model.evaluate(multi_window.val)
multi_performance['AR Stack RNN'] = arr_stacked_rnn_model.evaluate(multi_window.test, verbose=0)

In [ ]:
# print graph of the results
x = np.arange(len(multi_performance))
width = 0.3
metric_name = 'mean_absolute_error'
metric_index = lstm_model.metrics_names.index('mean_absolute_error')
val_mae = [v[metric_index] for v in multi_val_performance.values()]
test_mae = [v[metric_index] for v in multi_performance.values()]

plt.ylabel('mean_absolute_error, normalized]')
plt.bar(x - 0.17, val_mae, width, label='Validation')
plt.bar(x + 0.17, test_mae, width, label='Test')
plt.xticks(ticks=x, labels=multi_performance.keys(),
           rotation=45)
_ = plt.legend()

In [ ]:
input_w = 64
if DATA == "daily":
  output_w = 14
else:
  output_w = 24

def eval_dense_model(units, learning_rate, dropout):
  # Track progress
  mean_benchmark = []
  epochs_needed = []

  multi_window = WindowGenerator(input_width=input_w,
                                train_df=train_df, val_df=val_df, test_df=test_df,
                                label_width=output_w,
                                shift=output_w)

  units = int(units*1000)
  model = gen_dense_model(output_w, num_features, dropout, units)
  history = compile_and_fit(model, multi_window, opt=tf.optimizers.Adam(learning_rate=learning_rate))

  test_performance = model.evaluate(multi_window.val, verbose=0)
  mean_benchmark.append(-test_performance[1])
  m = statistics.mean(mean_benchmark)
  tf.keras.backend.clear_session()
  return (m)
 

def eval_lstm_model(units, learning_rate, dropout):
  mean_benchmark = []
  epochs_needed = []

  multi_window = WindowGenerator(input_width=input_w,
                                train_df=train_df, val_df=val_df, test_df=test_df,
                                label_width=output_w,
                                shift=output_w)
 
  units = int(units*1000)
  model = gen_lstm_model(output_w, num_features, dropout, units)
  history = compile_and_fit(model, multi_window, opt=tf.optimizers.Adam(learning_rate=learning_rate))
  
  test_performance = model.evaluate(multi_window.val, verbose=0)
  mean_benchmark.append(-test_performance[1])
  m = statistics.mean(mean_benchmark)
  tf.keras.backend.clear_session()
  return (m)

def eval_gru_model(units, learning_rate, dropout):
  mean_benchmark = []
  epochs_needed = []

  multi_window = WindowGenerator(input_width=input_w,
                                train_df=train_df, val_df=val_df, test_df=test_df,
                                label_width=output_w,
                                shift=output_w)
 
  units = int(units*1000)
  model = gen_gru_model(output_w, num_features, dropout, units)
  history = compile_and_fit(model, multi_window, opt=tf.optimizers.Adam(learning_rate=learning_rate))
  
  test_performance = model.evaluate(multi_window.val, verbose=0)
  mean_benchmark.append(-test_performance[1])
  m = statistics.mean(mean_benchmark)
  tf.keras.backend.clear_session()
  return (m)

def eval_ar_gru_model(units, learning_rate, dropout):
  mean_benchmark = []
  epochs_needed = []

  multi_window = WindowGenerator(input_width=input_w,
                                train_df=train_df, val_df=val_df, test_df=test_df,
                                label_width=output_w,
                                shift=output_w)
 
  units = int(units*1000)

  model = Arr_Rnn(output_w)
  model.put_gru(units, dropout)
  prediction, state = model.warmup(multi_window.example[0])

  history = compile_and_fit(model, multi_window, opt=tf.optimizers.Adam(learning_rate=learning_rate))
  
  test_performance = model.evaluate(multi_window.val, verbose=0)
  mean_benchmark.append(-test_performance[1])
  m = statistics.mean(mean_benchmark)
  tf.keras.backend.clear_session()
  return (m)

def eval_ar_lstm_model(units, learning_rate, dropout):
  mean_benchmark = []
  epochs_needed = []

  multi_window = WindowGenerator(input_width=input_w,
                                train_df=train_df, val_df=val_df, test_df=test_df,
                                label_width=output_w,
                                shift=output_w)
 
  units = int(units*1000)

  model = Arr_Rnn(output_w)
  model.put_lstm(units, dropout)
  prediction, state = model.warmup(multi_window.example[0])

  history = compile_and_fit(model, multi_window, opt=tf.optimizers.Adam(learning_rate=learning_rate))
  
  test_performance = model.evaluate(multi_window.val, verbose=0)
  mean_benchmark.append(-test_performance[1])
  m = statistics.mean(mean_benchmark)
  tf.keras.backend.clear_session()
  return (m)

def eval_ar_sirnn_model(units, learning_rate, dropout):
  mean_benchmark = []
  epochs_needed = []

  multi_window = WindowGenerator(input_width=input_w,
                                train_df=train_df, val_df=val_df, test_df=test_df,
                                label_width=output_w,
                                shift=output_w)
 
  units = int(units*1000)

  model = Arr_Rnn(output_w)
  model.put_simple_rnn(units, dropout)
  prediction, state = model.warmup(multi_window.example[0])

  history = compile_and_fit(model, multi_window, opt=tf.optimizers.Adam(learning_rate=learning_rate))
  
  test_performance = model.evaluate(multi_window.val, verbose=0)
  mean_benchmark.append(-test_performance[1])
  m = statistics.mean(mean_benchmark)
  tf.keras.backend.clear_session()
  return (m)

def eval_ar_strnn_model(units, learning_rate, dropout):
  mean_benchmark = []
  epochs_needed = []

  multi_window = WindowGenerator(input_width=input_w,
                                train_df=train_df, val_df=val_df, test_df=test_df,
                                label_width=output_w,
                                shift=output_w)
 
  units = int(units*1000)

  model = Arr_Rnn(output_w)
  model.put_stacked_rnn(units, dropout)
  prediction, state = model.warmup(multi_window.example[0])

  history = compile_and_fit(model, multi_window, opt=tf.optimizers.Adam(learning_rate=learning_rate))
  
  test_performance = model.evaluate(multi_window.val, verbose=0)
  mean_benchmark.append(-test_performance[1])
  m = statistics.mean(mean_benchmark)
  tf.keras.backend.clear_session()
  return (m)

# Bounded region of parameter space
pbounds_m = {'units': (0.1, 0.99),
           'learning_rate': (0.01, 0.299),
           'dropout': (0.01, 0.299)
          }


dense_optimizer = BayesianOptimization(
    f=eval_dense_model,
    pbounds=pbounds_m,
    verbose=2,
    random_state=1,
)

lstm_optimizer = BayesianOptimization(
    f=eval_lstm_model,
    pbounds=pbounds_m,
    verbose=2,
    random_state=1,
)

gru_optimizer = BayesianOptimization(
    f=eval_gru_model,
    pbounds=pbounds_m,
    verbose=2,
    random_state=1,
)

ar_gru_optimizer = BayesianOptimization(
    f=eval_ar_gru_model,
    pbounds=pbounds_m,
    verbose=2,
    random_state=1,
)

ar_lstm_optimizer = BayesianOptimization(
    f=eval_ar_lstm_model,
    pbounds=pbounds_m,
    verbose=2,
    random_state=1,
)

ar_sirnn_optimizer = BayesianOptimization(
    f=eval_ar_sirnn_model,
    pbounds=pbounds_m,
    verbose=2,
    random_state=1,
)

ar_strnn_optimizer = BayesianOptimization(
    f=eval_ar_strnn_model,
    pbounds=pbounds_m,
    verbose=2,
    random_state=1,
)

n_iter = 50
#start_time = time.time()
dense_optimizer.maximize(init_points=10, n_iter=n_iter,)
lstm_optimizer.maximize(init_points=10, n_iter=n_iter,)
gru_optimizer.maximize(init_points=10, n_iter=n_iter,)
ar_gru_optimizer.maximize(init_points=10, n_iter=n_iter,)
ar_lstm_optimizer.maximize(init_points=10, n_iter=n_iter,)
ar_sirnn_optimizer.maximize(init_points=10, n_iter=n_iter,)
ar_strnn_optimizer.maximize(init_points=10, n_iter=n_iter,)